In [1]:
import sys
import numpy
import re
from tqdm import tqdm
from keras.models import Sequential
from keras.layers import Dense
from keras.layers import Dropout
from keras.layers import LSTM
from keras.callbacks import ModelCheckpoint
from keras.utils import np_utils

c:\program files\python36\lib\site-packages\h5py\__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


In [2]:
f1 = "./Data/001ssb.txt"
f2 = "./Data/002ssb.txt"
f3 = "./Data/003ssb.txt"
f4 = "./Data/004ssb.txt"
f5 = "./Data/005ssb.txt"

In [3]:
raw_text = open(f1).read() + open(f2).read() + open(f3).read() + open(f4).read() + open(f5).read()

In [4]:
raw_text = raw_text.lower()

In [5]:
raw_text.replace(r'Page (\d+)\n', '')

'prologue \n"we should start back," gared urged as the woods began to grow dark around them. "the wildlings are \ndead." \n"do the dead frighten you?" ser waymar royce asked with just the hint of a smile. \ngared did not rise to the bait. he was an old man, past fifty, and he had seen the lordlings come and go. \n"dead is dead," he said. "we have no business with the dead." \n"are they dead?" royce asked softly. "what proof have we?" \n"will saw them," gared said. "if he says they are dead, that\'s proof enough for me." \nwill had known they would drag him into the quarrel sooner or later. he wished it had been later rather \nthan sooner. "my mother told me that dead men sing no songs," he put in. \n"my wet nurse said the same thing, will," royce replied. "never believe anything you hear at a woman\'s \ntit. there are things to be learned even from the dead." his voice echoed, too loud in the twilit forest. \npage 1\n\n"we have a long ride before us," gared pointed out. "eight days, ma

In [7]:
chars = sorted(list(set(raw_text)))
char_to_int = dict((c,i) for i,c in enumerate(chars))

In [8]:
n_chars = len(raw_text)
n_vocab = len(chars)

In [9]:
seq_length = 100
dataX = []
dataY = []

In [10]:
for i in tqdm(range(0, n_chars - seq_length, 1), desc="Building datasets"):
    seq_in = raw_text[i:i+seq_length]
    seq_out = raw_text[i + seq_length]
    dataX.append([char_to_int[char] for char in seq_in])
    dataY.append(char_to_int[seq_out])

Building datasets: 100%|█████████████████████████████████████████████████| 9630483/9630483 [01:10<00:00, 137325.23it/s]


In [13]:
n_patterns = len(dataX)
print("Total Patterns: ", n_patterns)

Total Patterns:  9630483


In [14]:
X = numpy.reshape(dataX, (n_patterns, seq_length, 1))
X = X/float(n_vocab)
y = np_utils.to_categorical(dataY)

In [15]:
model = Sequential()
model.add(LSTM(256, input_shape=(X.shape[1], X.shape[2]), return_sequences=True))
model.add(Dropout(0.2))
model.add(LSTM(256))
model.add(Dropout(0.2))
model.add(Dense(y.shape[1], activation='softmax'))

Instructions for updating:
keep_dims is deprecated, use keepdims instead


In [16]:
filepath = "./Checkpoints/weights-improvement-04-1.46159-bigger.hdf5"

In [17]:
model.load_weights(filepath)

In [18]:
model.compile(loss='categorical_crossentropy', optimizer='adam')

Instructions for updating:
keep_dims is deprecated, use keepdims instead


In [19]:
int_to_char = dict((i, c) for i, c in enumerate(chars))

In [20]:
start = numpy.random.randint(0, len(dataX)-1)
pattern = dataX[start]
print("Seed:")
print("\"", ''.join([int_to_char[value] for value in pattern]), "\"")

Seed:
" joffrey's queen-to-be. 
i wish the hound were here. the night of the battle, sandor clegane had come "


In [ ]:
for i in range(1000):
	x = numpy.reshape(pattern, (1, len(pattern), 1))
	x = x / float(n_vocab)
	prediction = model.predict(x, verbose=0)
	index = numpy.argmax(prediction)
	result = int_to_char[index]
	seq_in = [int_to_char[value] for value in pattern]
	sys.stdout.write(result)
	pattern.append(index)
	pattern = pattern[1:len(pattern)]